In [1]:
import pandas as pd
import numpy as np
from indels_func import is_indel, table_editing, indel_type
from mapping_func import create_exon_pos_table
import pickle

In [2]:
#Getting path
curr_dir = !pwd
pfam_version = "32"
in_path = curr_dir[0]+"/../3.parse_HMMER/hmm_domains/pfam-v"+pfam_version+"/"
chrom_path = curr_dir[0]+"/../1.parse_ExAC/parsed_filtered/"
chrom_filename = "parsed_filtered_chrom"
out_path = curr_dir[0]+"/domain_gene_exac/pfam-v"+pfam_version+"/"

#Reading the list of filtered domains
if (pfam_version != "32"):
    with open(curr_dir[0]+"/../5.domains_stats/pfam-v"+pfam_version+"/filtered10_list.pik", 'rb') as handle:
        filtered_domains_list10 = pickle.load(handle)
    filtered_domains_list10.sort()

#Reading list of all domains
if (pfam_version == "32"):
    with open(curr_dir[0]+"/../5.domains_stats/pfam-v"+pfam_version+"/human_domains_list.pik", 'rb') as handle:
        all_domains_list = pickle.load(handle)
else:
    with open(curr_dir[0]+"/../5.domains_stats/pfam-v"+pfam_version+"/all_domains_list.pik", 'rb') as handle:
        all_domains_list = pickle.load(handle)
all_domains_list.sort()
print "#(domains) = "+str(len(all_domains_list))

#Chromosome names
chromosome_names = ["1", "2", "3", "4", "5", "6", "7", "8", "9", "10", "11", "12", "13", "14", "15", "16", "17", "18", "19", "20", "21", "22", "X", "Y"]

#(domains) = 6510


In [8]:
%%time
for chrom in chromosome_names:
    
    #Loading the ExAC parsed data of this chromosome
    fields = ["chrom", "pos", "ref", "alt", "filter", "AC", "AC_AFR", "AC_AMR", "AC_Adj", "AC_EAS", "AC_FIN", "AC_Het", "AC_Hom", "AC_NFE", "AC_OTH", "AC_SAS", 
              "AF", "AN", "AN_AFR", "AN_AMR", "AN_Adj", "AN_EAS", "AN_FIN", "AN_NFE", "AN_OTH", "AN_SAS", "prot_pos", "amino_acids", "codons", "ENSP", 
              "SWISSPROT", "SIFT", "PolyPhen","clin_sig", "conseq", "feature", "strand", "coverage"]
                #More fields that might be interesting:  feature_type, domains, , gene
    chrom_csv = pd.read_csv(chrom_path+chrom_filename+chrom+".csv", sep='\t', usecols=fields,
                           dtype={"AC": int, "AC_AFR": int, "AC_AMR": int, "AC_Adj": int, "AC_EAS": int,
                               "AC_FIN": int, "AC_Het": int, "AC_Hom": int, "AC_NFE": int, "AC_OTH": int, "AC_SAS": int, "AF": float, "AN": int, "AN_AFR": int,
                               "AN_AMR": int, "AN_Adj": int, "AN_EAS": int, "AN_FIN": int, "AN_NFE": int, "AN_OTH": int, "AN_SAS": int, "prot_pos": str})
    chrom_csv = chrom_csv.sort_values(by=["pos"])
    chrom_csv = chrom_csv.reset_index(drop=True)
    chrom_csv.fillna('', inplace=True)
    chrom_csv["comments"] = ""

    for domain_name in all_domains_list:

        #Get the canonic protein id for the domain
        with open(curr_dir[0]+"/../4.parse_Uniprot/domains_canonic_prot/pfam-v"+pfam_version+"/"+domain_name+"_canonic_prot.pik", 'rb') as handle:
            canonic_protein = pickle.load(handle)
    
        filename = domain_name+".csv"
        domain_data = pd.read_csv(in_path+filename, sep='\t', index_col=0, dtype={"chrom_num": str})
        #Sort the domain data
        sorted_domain_data = domain_data.sort_values(by=["chrom_num", "gene", "TargetStart"])
        sorted_domain_data = sorted_domain_data.reset_index(drop=True)

        #Filtering the domain data relevant to this chromosome
        domain_chrom_data = sorted_domain_data[sorted_domain_data["chrom_num"] == chrom]

        #Getting a list of all the relevant ensembl gene ids for this chromosome
        domain_ens_genes = (domain_chrom_data["gene"]).unique()
        #domain_ens_genes_all.extend(domain_ens_genes)

        #If this domain have no genes on this chromosome, continue to the next domain
        if (len(domain_ens_genes) == 0):
            print "Finished domain "+domain_name
            continue
        
        for ens_gene in domain_ens_genes:
        
            #Filtering the domain data for this gene according to the canonical protein id
            canonic_prot = canonic_protein[ens_gene]
            canonic_prot_t = canonic_prot[:canonic_prot.find(".")] #Trimming the ".#" at the end
            domain_gene_table = domain_chrom_data[domain_chrom_data["prot"] == canonic_prot]
            #Making sure that if two HMM-matches overlaps, the higher bit score will come first in the table
            domain_gene_table = domain_gene_table.sort_values(by="BitScore", ascending=False)
            domain_gene_name = domain_gene_table["hugoSymbol"].unique()[0]
            if (len(domain_gene_table["hugoSymbol"].unique()) > 1):
                print functionNameAsString+" Error: "+ens_gene+": more than one Hugo symbol"  #sanity check

            #Creating a table of the exons for this gene, according to the canonical protein
            chrom_raw_data = domain_gene_table["chromosome"].unique()[0] #there should be only one element here
            if (len(domain_gene_table["chromosome"].unique()) > 1):
                print functionNameAsString+" Error: "+ens_gene+": more than one chromosome raw data" #sanity check
            targetid = domain_gene_table["#TargetID"].unique()[0]
            exon_table = create_exon_pos_table(chrom_raw_data, targetid)

            #Filtering the chromosome data to the gene exons region
            exons_start_pos = min(exon_table["start_pos"][0],exon_table["start_pos"][len(exon_table)-1]) #in case of complelemt, the minimal position could be at the last row
            exons_end_pos = max(exon_table["end_pos"][0],exon_table["end_pos"][len(exon_table)-1]) #in case of complelemt, the maximal position could be at the first row
            chrom_gene_table = chrom_csv[chrom_csv["pos"] >= int(exons_start_pos)][chrom_csv["pos"] <= int(exons_end_pos)][chrom_csv["ENSP"] == canonic_prot_t]
            chrom_gene_table = chrom_gene_table.reset_index(drop=True)
            
            #Adding chrom column to the table
            chrom_gene_table["chrom"] = chrom

            #Handling indels
            indels_table = table_editing(chrom_gene_table)
            
            !mkdir -p domain_gene_exac/pfam-v32/$domain_name
            !mkdir -p domain_gene_exac/pfam-v32/$domain_name/$ens_gene
            chrom_gene_table.to_csv(out_path+domain_name+"/"+ens_gene+"/chrom_gene_table.csv",sep='\t')
            indels_table.to_csv(out_path+domain_name+"/"+ens_gene+"/indels_table.csv",sep='\t')
            exon_table.to_csv(out_path+domain_name+"/"+ens_gene+"/exon_table.csv",sep='\t')
            
            print "Finished gene "+ens_gene
        print "Finished domain "+domain_name
    print "Finished chromosome "+chrom

Finished gene ENSG00000117450.9
Finished gene ENSG00000117592.8
Finished domain 1-cysPrx_C
Finished gene ENSG00000175793.10
Finished domain 14-3-3
Finished gene ENSG00000092621.7
Finished domain 2-Hacid_dh
Finished gene ENSG00000092621.7
Finished domain 2-Hacid_dh_C
Finished gene ENSG00000137992.10
Finished domain 2-oxoacid_dh
Finished domain 2-oxogl_dehyd_N
Finished domain 23ISL
Finished domain 2Fe-2S_thioredx
Finished gene ENSG00000083444.12
Finished gene ENSG00000117385.11
Finished domain 2OG-FeII_Oxy
Finished domain 2OG-FeII_Oxy_2
Finished gene ENSG00000117385.11
Finished gene ENSG00000135766.8
Finished domain 2OG-FeII_Oxy_3
Finished gene ENSG00000135766.8
Finished domain 2OG-FeII_Oxy_4
Finished domain 3-HAO
Finished gene ENSG00000014914.15
Finished domain 3-PAP
Finished gene ENSG00000117308.10
Finished gene ENSG00000203857.5
Finished gene ENSG00000203859.5
Finished domain 3Beta_HSD
Finished domain 3HCDH
Finished domain 3HCDH_N
Finished domain 40S_S4_C
Finished domain 40S_SA_C
Fini

Finished gene ENSG00000155363.14
Finished domain AAA_30
Finished gene ENSG00000123836.10
Finished gene ENSG00000153187.12
Finished domain AAA_33
Finished domain AAA_34
Finished gene ENSG00000143748.13
Finished domain AAA_5
Finished gene ENSG00000185842.10
Finished domain AAA_6
Finished gene ENSG00000185842.10
Finished domain AAA_7
Finished gene ENSG00000185842.10
Finished domain AAA_8
Finished gene ENSG00000185842.10
Finished domain AAA_9
Finished domain AAA_assoc_2
Finished gene ENSG00000185842.10
Finished domain AAA_lid_1
Finished gene ENSG00000185842.10
Finished domain AAA_lid_11
Finished gene ENSG00000143748.13
Finished domain AAA_lid_3
Finished domain AAA_lid_5
Finished domain AAA_lid_7
Finished domain AAR2
Finished domain AARP2CN
Finished domain AATF-Che1
Finished domain AA_kinase
Finished domain AA_permease
Finished domain AA_permease_2
Finished domain AA_permease_C
Finished domain AA_permease_N
Finished gene ENSG00000117262.14
Finished gene ENSG00000188092.10
Finished gene ENSG

Finished gene ENSG00000160710.11
Finished domain A_deamin
Finished gene ENSG00000116337.11
Finished gene ENSG00000116748.15
Finished domain A_deaminase
Finished domain A_deaminase_N
Finished domain Aa_trans
Finished domain AbLIM_anchor
Finished domain AbfB
Finished domain Abhydro_lipase
Finished gene ENSG00000143819.8
Finished gene ENSG00000172031.6
Finished domain Abhydrolase_1
Finished gene ENSG00000011009.6
Finished gene ENSG00000143353.7
Finished domain Abhydrolase_2
Finished gene ENSG00000188984.7
Finished gene ENSG00000204518.2
Finished domain Abhydrolase_3
Finished gene ENSG00000172031.6
Finished domain Abhydrolase_6
Finished domain Abi_HHR
Finished domain Acatn
Finished domain Acetyltransf_1
Finished domain Acetyltransf_10
Finished domain Acetyltransf_13
Finished domain Acetyltransf_16
Finished domain Acetyltransf_2
Finished domain Acetyltransf_3
Finished domain Acetyltransf_7
Finished domain Acetyltransf_CG
Finished domain Acid_PPase
Finished domain Aconitase
Finished domain A

Finished domain Apolipoprotein
Finished domain Apt1
Finished domain Apyrase
Finished domain Aquarius_N
Finished domain Arc_C
Finished domain Arc_trans_TRASH
Finished gene ENSG00000176261.11
Finished domain Archease
Finished gene ENSG00000065135.7
Finished gene ENSG00000117280.8
Finished gene ENSG00000132698.9
Finished gene ENSG00000143545.4
Finished gene ENSG00000143622.6
Finished gene ENSG00000143761.9
Finished gene ENSG00000143862.3
Finished gene ENSG00000168118.7
Finished gene ENSG00000169213.6
Finished domain Arf
Finished gene ENSG00000084070.7
Finished gene ENSG00000088280.14
Finished gene ENSG00000131584.14
Finished domain ArfGap
Finished domain Arfaptin
Finished domain Arg_tRNA_synt_N
Finished gene ENSG00000116771.5
Finished domain Arginase
Finished domain Arginosuc_synth
Finished gene ENSG00000092847.6
Finished gene ENSG00000126070.14
Finished gene ENSG00000134698.10
Finished domain ArgoL1
Finished gene ENSG00000092847.6
Finished gene ENSG00000126070.14
Finished gene ENSG000001

Finished domain Biotin_carb_C
Finished domain Biotin_carb_N
Finished gene ENSG00000137992.10
Finished domain Biotin_lipoyl
Finished gene ENSG00000178096.8
Finished domain BolA
Finished domain Bombesin
Finished gene ENSG00000134690.6
Finished domain Borealin
Finished domain Branch
Finished gene ENSG00000163531.11
Finished domain Bravo_FIGEY
Finished gene ENSG00000117133.6
Finished domain Brix
Finished gene ENSG00000143157.7
Finished domain BrkDBD
Finished domain Bromo_TP
Finished gene ENSG00000116539.6
Finished gene ENSG00000137948.14
Finished gene ENSG00000197323.6
Finished domain Bromodomain
Finished domain Btz
Finished domain Bud13
Finished domain Bystin
Finished gene ENSG00000153029.10
Finished gene ENSG00000158473.6
Finished gene ENSG00000158477.6
Finished gene ENSG00000158481.8
Finished gene ENSG00000158485.6
Finished gene ENSG00000158488.11
Finished gene ENSG00000162706.8
Finished domain C1-set
Finished domain C12orf66_like
Finished gene ENSG00000183888.4
Finished domain C1ORF64


...

Finished domain Reprolysin_5
Finished domain Requiem_N
Finished domain Rer1
Finished domain ResIII
Finished domain Resistin
Finished domain Reticulon
Finished domain Retinal
Finished domain Retrotrans_gag
Finished domain Rft-1
Finished domain Rgp1
Finished domain RhoGAP
Finished domain RhoGAP-FF1
Finished domain RhoGEF
Finished domain RhoGEF67_u1
Finished domain RhoGEF67_u2
Finished domain Rho_Binding
Finished domain Rho_GDI
Finished domain Rhodanese
Finished domain Rhodanese_C
Finished domain Rhodopsin_N
Finished domain Rhomboid
Finished domain Rhomboid_SP
Finished domain Rib_5-P_isom_A
Finished domain Rib_hydrolayse
Finished domain Rib_recp_KP_reg
Finished domain Ribo_biogen_C
Finished domain Ribonuc_2-5A
Finished domain Ribonuc_L-PSP
Finished domain Ribonuc_P_40
Finished domain Ribonuc_red_lgC
Finished domain Ribonuc_red_lgN
Finished domain Ribonuc_red_sm
Finished domain Ribonucleas_3_3
Finished domain Ribonuclease_3
Finished domain Ribonuclease_T2
Finished domain Ribophorin_I
Finis

Finished domain Sulfotransfer_3
Finished domain Sun2_CC2
Finished domain Suppressor_APC
Finished domain Surfac_D-trimer
Finished domain Surp
Finished domain Sushi
Finished domain Sushi_2
Finished domain Suv3_C_1
Finished domain Suv3_N
Finished domain Swi3
Finished domain Swi5
Finished domain Sybindin
Finished domain Syja_N
Finished domain Symplekin_C
Finished domain Synaphin
Finished domain Synapsin
Finished domain Synapsin_C
Finished domain Synapsin_N
Finished domain Synaptobrevin
Finished domain Synaptonemal_3
Finished domain Syncollin
Finished domain Syndecan
Finished domain Syntaphilin
Finished domain Syntaxin
Finished domain Syntaxin-18_N
Finished domain Syntaxin-5_N
Finished domain Syntaxin-6_N
Finished domain Syntaxin_2
Finished domain Synuclein
Finished domain T-box
Finished domain T-box_assoc
Finished domain T4_deiodinase
Finished domain TACC_C
Finished domain TACI-CRD2
Finished domain TAD2
Finished domain TAF
Finished domain TAF1D
Finished domain TAF1_subA
Finished domain TAF

Finished domain Tex_YqgF
Finished domain Tfb2
Finished domain Tfb2_C
Finished domain Tfb4
Finished domain Tfb5
Finished domain Thg1
Finished domain Thg1C
Finished domain ThiF
Finished domain ThiS
Finished domain Thioesterase
Finished domain Thiolase_C
Finished domain Thiolase_N
Finished domain Thioredox_DsbH
Finished domain Thioredoxin
Finished domain Thioredoxin_12
Finished domain Thioredoxin_13
Finished domain Thioredoxin_14
Finished domain Thioredoxin_15
Finished domain Thioredoxin_16
Finished domain Thioredoxin_2
Finished domain Thioredoxin_6
Finished domain Thioredoxin_7
Finished domain Thioredoxin_8
Finished domain Tho2
Finished domain Thoc2
Finished domain Thr_synth_N
Finished domain Thrombin_light
Finished domain Thymidylat_synt
Finished domain Thymidylate_kin
Finished domain Thymopoietin
Finished gene ENSG00000154620.5
Finished domain Thymosin
Finished domain Thyroglob_assoc
Finished domain Thyroglobulin_1
Finished domain Tiam_CC_Ex
Finished domain Tim17
Finished domain Tim29


Finished domain Vert_IL3-reg_TF
Finished domain Vezatin
Finished domain Vg_Tdu
Finished domain Vinculin
Finished domain VitD-bind_III
Finished domain Vitellogenin_N
Finished domain Vma12
Finished domain Voldacs
Finished domain Voltage_CLC
Finished domain Vps16_C
Finished domain Vps16_N
Finished domain Vps23_core
Finished domain Vps26
Finished domain Vps35
Finished domain Vps36_ESCRT-II
Finished domain Vps39_1
Finished domain Vps39_2
Finished domain Vps4_C
Finished domain Vps5
Finished domain Vps51
Finished domain Vps52
Finished domain Vps53_N
Finished domain Vps54
Finished domain Vps54_N
Finished domain Vps55
Finished domain Vps8
Finished domain Vta1
Finished domain Vta1_C
Finished domain W2
Finished domain WAC_Acf1_DNA_bd
Finished domain WAP
Finished domain WAPL
Finished domain WASH-7_C
Finished domain WASH-7_N
Finished domain WASH-7_mid
Finished domain WASH_WAHD
Finished domain WBP-1
Finished domain WBS28
Finished domain WBS_methylT
Finished domain WD-3
Finished gene ENSG00000092377.

Finished domain zf-RING_4
Finished domain zf-RING_5
Finished domain zf-RING_6
Finished domain zf-RING_9
Finished domain zf-RING_UBOX
Finished domain zf-RNPHF
Finished domain zf-RRN7
Finished domain zf-RanBP
Finished domain zf-SAP30
Finished domain zf-SCNM1
Finished domain zf-SNAP50_C
Finished domain zf-Sec23_Sec24
Finished domain zf-TAZ
Finished domain zf-TFIIIC
Finished domain zf-TRAF
Finished domain zf-TRAF_2
Finished domain zf-TRM13_CCCH
Finished domain zf-Tim10_DDP
Finished domain zf-U1
Finished domain zf-U11-48K
Finished domain zf-UBP
Finished domain zf-UBP_var
Finished domain zf-UBR
Finished domain zf-WRNIP1_ubi
Finished domain zf-ZPR1
Finished domain zf-dskA_traR
Finished domain zf-met
Finished domain zf-nanos
Finished domain zf-piccolo
Finished domain zf-primase
Finished domain zf-rbx1
Finished domain zf-tcix
Finished domain zf_C2H2_10
Finished domain zf_C2H2_6
Finished domain zf_C2H2_ZHX
Finished domain zf_C2HC_14
Finished domain zf_CCCH_4
Finished domain zf_CCCH_5
Finished do

In [5]:
#Save an updated domains list
with open(curr_dir[0]+"/../5.domains_stats/pfam-v"+pfam_version+"/regular_human_domains_list.pik", 'wb') as handle:
    pickle.dump(domains_files, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [6]:
len(domains_files)

6503